<a href="https://colab.research.google.com/github/Utpal-Mishra/Optimal-Control-Therapy-4-Cancer-Treatment/blob/main/OptimalControlTherapy4CancerTreatmentTASK8.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## **IMPORT** 

### GOOGLE DRIVE

In [ ]:
from google.colab import drive # import google drive into colaboratory
drive.mount("/content/drive")  # mount drive and the files

print("\nGOOGLE DRIVE is MOUNTED!!!")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).

GOOGLE DRIVE is MOUNTED!!!


### LIBRARIES

In [ ]:
import pandas as pd              # import pandas to use high-performance data structure and for data analysis
import numpy as np               # import numpy to evaluate data using mathematical operations
import matplotlib.pyplot as plt  # import matplotlib for 2D graphs and plots 
import seaborn as sns            # import seaborn for visualization 
import plotly.express as px      # import plotly for interactive plots
import plotly.graph_objects as go

import sys                       # import sys to manipulate Python runtime environment
sys.setrecursionlimit(100000)    # setting recursion limit for execusion

from sklearn import preprocessing                  # import preprocessing from sklearn statistical computations
from sklearn.preprocessing import StandardScaler   # import standardscaler for scaling the feature variables
scale = StandardScaler()                           # creating scaling object

print("LIBRARIES are IMPORTED!!!")

LIBRARIES are IMPORTED!!!


### DATA 

In [ ]:
path = "/content/drive/MyDrive/UCD Research/Data.xlsx"   # set the path of the .csv file from drive

data = pd.read_excel(path)                                                                 # using read_csv() of pandas library to read the data file 
print("DATA is IMPORTED!!!")

print("\nDimensions of Data: ", data.shape)                                                # printing the dimensions of the dataset

DATA is IMPORTED!!!

Dimensions of Data:  (29, 48)


In [ ]:
#data.head() # or data.head(n), n=5 by default
# taking a look at the first 5 rows of the data using .head() 
data.sort_values("Patient No.")
data.head()

Patient No. start date  ...  Date of last sample analysed Unnamed: 47
0  0006 00007 RJW 2001-01-22  ...                    2008-06-12         NaN
1  0004 00003-CAR 2000-08-29  ...                    2007-09-07         NaN
2   0003 00002 CL 2000-08-08  ...                    2008-01-09         NaN
3  0011 00003  LM 2000-11-14  ...                    2003-08-19         NaN
4  0001 00004 AJR 2000-08-04  ...                    2007-01-11         NaN

[5 rows x 48 columns]

## **EXPLORATORY DATA ANALYSIS**

### DEALING WITH EMPTY/ NULL VALUES

ANALYZING TOTOAL EMPTY VALUES IN EACH FEATURE VARIABLE

In [ ]:
if data.isna().sum().sum() != 0:
  print("EMPTY VALUES EXIST IN THE DATA\n\nFollowing is a list of feature variable with their respective null values count:\n", data.isna().sum())  #or data.applymap(np.isreal).all()
# listing the total number of null values in each column of the dataset

EMPTY VALUES EXIST IN THE DATA

Following is a list of feature variable with their respective null values count:
 Patient No.                      0
start date                       0
Age                              0
sex                              0
Weight (kg)                      0
Baseline                         1
3                                2
6                                5
9                                4
12                               6
15                              17
18                              12
21                              12
24                              11
27                              11
30                              11
33                               6
36                               7
39                               5
42                               7
45                               7
48                              10
51                              12
54                              10
57                              11
60         

FILLING NULL VALUES OF THE NUMERICAL FEATURES WITH THEIR MEANS

REMOVING NULL FEATURE VARIABLES


REPLACE 'Unknown' WITH EMPTY VALUES IN CATEGORICAL VARIABLES

In [ ]:
data = data.fillna(data.mean())                                                        # filling null celss of feature variables with the mean value of non-empty cells
#data = data.fillna("Unknown")                                                          # filling left over empty categorical features with 'Unknown' label

data[51] = data[51].fillna(0)
data[51] = data[51].replace(" ", 0)
data[51] = data[51].astype(str).astype(float)

data[105] = data[105].fillna(0)
data[105] = data[105].replace(" ", 0)
data[105] = data[105].astype(str).astype(float)

data[12] = data[12].fillna(0)
data[12] = data[12].replace(" ", 0)
data[12] = data[12].astype(str).astype(float)

data.Baseline = data.Baseline.fillna(0)
data.Baseline = data.Baseline.replace(" ", 0)
data.Baseline = data.Baseline.astype(str).astype(int)

data["Unnamed: 47"] = data["Unnamed: 47"].fillna('Unknown')

print("EMPTY VALUES: ", data.isna().sum().sum())  #or data.applymap(np.isreal).all()   # listing the total number of null values in each column of the dataset

EMPTY VALUES:  0


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: FutureWarning:

DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.



In [ ]:
from google.colab import files

data.to_csv("data.csv")
files.download("data.csv")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## **MODELING**

### **Data**

In [ ]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn import preprocessing, svm
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression

import scipy
from scipy.integrate import odeint, solve_ivp
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

In [ ]:
df = pd.DataFrame(data)

df.sex = data.sex.apply(lambda x: 0 if x == "F" else 1)
df["Weight/mean(Weight)-1"] = (df["Weight (kg)"]/round(df["Weight (kg)"].mean(), 1)) - 1
df["Age/mean(Age)-1"] = (df["Age "]/round(df["Age "].mean(), 1)) - 1
df["1 - sex"] = 1 - df["sex"]
# df.head()

In [ ]:
Qa = 12.8
Qb = 258 
Q1 = 12.7
Q2 = 0.8
Q3 = -2.1
Q4 = 61.0
ka = 0.61

CL = Qa + Q1*df["Weight/mean(Weight)-1"] + Q2*df['sex'] - Q2*df["1 - sex"] + Q3*df["Age/mean(Age)-1"]
v  = Qb + Q4*df['sex'] - Q4*df["1 - sex"]
df["CL"] = CL
df["v"] = v

df = pd.DataFrame(data[['Patient No.', 'start date', 'Age ', 'Age/mean(Age)-1', 'sex', '1 - sex', 'Weight (kg)', 'Weight/mean(Weight)-1', 
       'Baseline', 'CL', 'v', 3, 6, 9, 12, 15, 18, 21, 24, 27, 30, 33, 36, 39, 42,
       45, 48, 51, 54, 57, 60, 63, 66, 69, 72, 75, 78, 81, 84, 87, 90, 93,
       96, 99, 102, 105, 108, 111, 114, 117, 120,
       'Date of last sample analysed']])
df.head()

Patient No. start date  ...    120  Date of last sample analysed
0  0006 00007 RJW 2001-01-22  ...  0.004                    2008-06-12
1  0004 00003-CAR 2000-08-29  ...  0.004                    2007-09-07
2   0003 00002 CL 2000-08-08  ...  0.004                    2008-01-09
3  0011 00003  LM 2000-11-14  ...  0.004                    2003-08-19
4  0001 00004 AJR 2000-08-04  ...  0.004                    2007-01-11

[5 rows x 52 columns]

## **TASK 7**

### **4 Dosage Per Day at Variable Time PK Model**

**Available Variable Time Intervals**

In [ ]:
time = []
for t1 in range(8, 12):
  for t2 in range(4, 8):
    for t3 in range(4, 8):
      for t4 in range(4, 8):
        if(t1+t2+t3+t4 == 24):
          # print(t1, t2, t3, t4,"\n")
          time.append([t1, t2, t3, t4])
  
time

8 12 17 24
8 12 18 24
8 12 19 24
8 13 17 24
8 13 18 24
8 13 19 24
8 13 20 24
8 14 18 24
8 14 19 24
8 14 20 24
8 15 19 24
8 15 20 24
9 13 17 24
9 13 18 24
9 13 19 24
9 13 20 24
9 14 18 24
9 14 19 24
9 14 20 24
9 15 19 24
9 15 20 24
9 16 20 24
10 14 18 24
10 14 19 24
10 14 20 24
10 15 19 24
10 15 20 24
10 16 20 24
11 15 19 24
11 15 20 24
11 16 20 24


**Fixed Dosage of 400mg with Variable Time Interval for 4 Dosage Administration**

In [ ]:
def pkmodel(x, t):
  CL=14.3 
  ka=0.61 
  v=347   
  chig = x[0]
  chib = x[1]

  #dchigdt = -ka*chig
  #dchibdt = ka*chig - CL*(chib/v)
  dydt = [-ka*chig, ka*chig - CL*(chib/v)]
  return dydt

D = 400
f = 1
xi = [D*f, 0]
time = []

for t1 in range(8, 12):

  for t2 in range(4, 8):

    for t3 in range(4, 8):

      for t4 in range(4, 8):

        if(t1+t2+t3+t4 == 24):

          # print(t1, t2, t3, t4,"\n")
          time.append([t1, t2, t3, t4])
          
          fig = make_subplots(rows=1, cols=3, specs=[[{}, {}, {}]], subplot_titles=("Time vs chig", "", "Time vs chib"))
          
          # first dose
          t_eval = np.linspace(0, t1, 80)
          Y = (odeint(pkmodel, xi, t_eval))

          fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 0], name = "chig: change in amount of Imatinib in the gastrointestinal tract at D = 400mg"), row=1, col=1)
          fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 1], name = "chib: change in the amount of Imatinib in the blood with time at D = 400mg"), row=1, col=3)
          fig.update_layout(height=500, width=1200, title_text="Optimal Control Therapy for Cancer Treatment " + str(t1) + " :: " + str(t2) + " :: " + str(t3) + " :: " + str(t4)) 
          fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 1)
          fig.update_yaxes(title_text = "chig", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 1)
          fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 3)
          fig.update_yaxes(title_text = "chib", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 3)
          
          # second dose
          t_eval = np.linspace(t1, t1+t2, 80)
          Y = (odeint(pkmodel, xi, t_eval))

          fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 0], name = "chig: change in amount of Imatinib in the gastrointestinal tract at D = 400mg"), row=1, col=1)
          fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 1], name = "chib: change in the amount of Imatinib in the blood with time at D = 400mg"), row=1, col=3)
          fig.update_layout(height=500, width=1200, title_text="Optimal Control Therapy for Cancer Treatment " + str(t1) + " :: " + str(t2) + " :: " + str(t3) + " :: " + str(t4)) 
          fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 1)
          fig.update_yaxes(title_text = "chig", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 1)
          fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 3)
          fig.update_yaxes(title_text = "chib", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 3)
          
          # third dose
          t_eval = np.linspace(t1+t2, t1+t2+t3, 80)
          Y = (odeint(pkmodel, xi, t_eval))

          fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 0], name = "chig: change in amount of Imatinib in the gastrointestinal tract at D = 400mg"), row=1, col=1)
          fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 1], name = "chib: change in the amount of Imatinib in the blood with time at D = 400mg"), row=1, col=3)
          fig.update_layout(height=500, width=1200, title_text="Optimal Control Therapy for Cancer Treatment " + str(t1) + " :: " + str(t2) + " :: " + str(t3) + " :: " + str(t4)) 
          fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 1)
          fig.update_yaxes(title_text = "chig", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 1)
          fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 3)
          fig.update_yaxes(title_text = "chib", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 3)
          
          # fourth dose
          t_eval = np.linspace(t1+t2+t3, t1+t2+t3+t4, 80)
          Y = (odeint(pkmodel, xi, t_eval))

          fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 0], name = "chig: change in amount of Imatinib in the gastrointestinal tract at D = 400mg"), row=1, col=1)
          fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 1], name = "chib: change in the amount of Imatinib in the blood with time at D = 400mg"), row=1, col=3)
          fig.update_layout(height=500, width=1200, title_text="Optimal Control Therapy for Cancer Treatment " + str(t1) + " :: " + str(t2) + " :: " + str(t3) + " :: " + str(t4)) 
          fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 1)
          fig.update_yaxes(title_text = "chig", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 1)
          fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 3)
          fig.update_yaxes(title_text = "chib", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 3)
          
          fig.show()

**Fixed Dosage of 400mg with Variable Time Interval for 4 Dosage Administration for all Patients**

In [ ]:
# def pkmodel(x, t, CL, v):
#     CL, v = CL, v
#     #CL=14.3 
#     ka=0.61 
#     #v=347   
#     chig = x[0]
#     chib = x[1]
  
#     #dchigdt = -ka*chig
#     #dchibdt = ka*chig - CL*(chib/v)
#     dydt = [-ka*chig, ka*chig - CL*(chib/v)]
#     return dydt

# D = 400
# f = 1
# xi = [D*f, 0]
# time = []

# for t1 in range(8, 12):

#   for t2 in range(4, 8):

#     for t3 in range(4, 8):

#       for t4 in range(4, 8):

#         if(t1+t2+t3+t4 == 24):

#           # print(t1, t2, t3, t4,"\n")
#           time.append([t1, t2, t3, t4])
          
#           fig = make_subplots(rows=1, cols=3, specs=[[{}, {}, {}]], subplot_titles=("Time vs chig", "", "Time vs chib"))
          
#           for i in range(df.shape[0]):

#               print("\nPatient: ", df["Patient No."][i], " :: Clearance: ", df["CL"][i], " :: Volumne: ", df["v"][i], "\n")
#               #params = (df["CL"][i], df["v"][i])
#               CL = df["CL"][i]
#               v  = df["v"][i]
              
#               # first dose
#               t_eval = np.linspace(0, t1, 80)
#               Y = odeint(pkmodel, xi, t_eval, args = (CL, v))

#               fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 0], name = "chig: change in amount of Imatinib in the gastrointestinal tract at D = 400mg"), row=1, col=1)
#               fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 1], name = "chib: change in the amount of Imatinib in the blood with time at D = 400mg"), row=1, col=3)
#               fig.update_layout(height=500, width=1200, title_text="Optimal Control Therapy for Cancer Treatment " + str(t1) + " :: " + str(t2) + " :: " + str(t3) + " :: " + str(t4)) 
#               fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 1)
#               fig.update_yaxes(title_text = "chig", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 1)
#               fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 3)
#               fig.update_yaxes(title_text = "chib", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 3)
              
#               # second dose
#               t_eval = np.linspace(t1, t1+t2, 80)
#               Y = odeint(pkmodel, xi, t_eval, args = (CL, v))

#               fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 0], name = "chig: change in amount of Imatinib in the gastrointestinal tract at D = 400mg"), row=1, col=1)
#               fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 1], name = "chib: change in the amount of Imatinib in the blood with time at D = 400mg"), row=1, col=3)
#               fig.update_layout(height=500, width=1200, title_text="Optimal Control Therapy for Cancer Treatment " + str(t1) + " :: " + str(t2) + " :: " + str(t3) + " :: " + str(t4)) 
#               fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 1)
#               fig.update_yaxes(title_text = "chig", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 1)
#               fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 3)
#               fig.update_yaxes(title_text = "chib", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 3)
              
#               # third dose
#               t_eval = np.linspace(t1+t2, t1+t2+t3, 80)
#               Y = odeint(pkmodel, xi, t_eval, args = (CL, v))

#               fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 0], name = "chig: change in amount of Imatinib in the gastrointestinal tract at D = 400mg"), row=1, col=1)
#               fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 1], name = "chib: change in the amount of Imatinib in the blood with time at D = 400mg"), row=1, col=3)
#               fig.update_layout(height=500, width=1200, title_text="Optimal Control Therapy for Cancer Treatment " + str(t1) + " :: " + str(t2) + " :: " + str(t3) + " :: " + str(t4)) 
#               fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 1)
#               fig.update_yaxes(title_text = "chig", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 1)
#               fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 3)
#               fig.update_yaxes(title_text = "chib", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 3)
              
#               # fourth dose
#               t_eval = np.linspace(t1+t2+t3, t1+t2+t3+t4, 80)
#               Y = odeint(pkmodel, xi, t_eval, args = (CL, v))

#               fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 0], name = "chig: change in amount of Imatinib in the gastrointestinal tract at D = 400mg"), row=1, col=1)
#               fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 1], name = "chib: change in the amount of Imatinib in the blood with time at D = 400mg"), row=1, col=3)
#               fig.update_layout(height=500, width=1200, title_text="Optimal Control Therapy for Cancer Treatment " + str(t1) + " :: " + str(t2) + " :: " + str(t3) + " :: " + str(t4)) 
#               fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 1)
#               fig.update_yaxes(title_text = "chig", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 1)
#               fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 3)
#               fig.update_yaxes(title_text = "chib", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 3)
              
#               fig.show()

**Different Dosages with Variable Time Interval for 4 Dosage Administration**

In [ ]:
def pkmodel(x, t):
  CL=14.3 
  ka=0.61 
  v=347   
  chig = x[0]
  chib = x[1]

  #dchigdt = -ka*chig
  #dchibdt = ka*chig - CL*(chib/v)
  dydt = [-ka*chig, ka*chig - CL*(chib/v)]
  return dydt

Dose = np.arange(100, 500, 100)
f = 1

for t1 in range(8, 12):

  for t2 in range(4, 8):

    for t3 in range(4, 8):

      for t4 in range(4, 8):

        if(t1+t2+t3+t4 == 24):

          
          for i in Dose:
            D = i
            xi = [D*f, 0]
             
            fig = make_subplots(rows=1, cols=3, specs=[[{}, {}, {}]], subplot_titles=("Time vs chig", "", "Time vs chib"))
            # first dose
            t_eval = np.linspace(0, t1, 80)
            Y = (odeint(pkmodel, xi, t_eval))

            fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 0], name = "chig: change in amount of Imatinib in the gastrointestinal tract at D = "+str(i)+"mg"), row=1, col=1)
            fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 1], name = "chib: change in the amount of Imatinib in the blood with time at D = "+str(i)+"mg"), row=1, col=3)
            fig.update_layout(height=500, width=1200, title_text="Optimal Control Therapy for Cancer Treatment " + str(t1) + " :: " + str(t2) + " :: " + str(t3) + " :: " + str(t4)) 
            fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 1)
            fig.update_yaxes(title_text = "chig", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 1)
            fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 3)
            fig.update_yaxes(title_text = "chib", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 3)
            
            # second dose
            t_eval = np.linspace(t1, t1+t2, 80)
            Y = (odeint(pkmodel, xi, t_eval))

            fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 0], name = "chig: change in amount of Imatinib in the gastrointestinal tract at D = "+str(i)+"mg"), row=1, col=1)
            fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 1], name = "chib: change in the amount of Imatinib in the blood with time at D = "+str(i)+"mg"), row=1, col=3)
            fig.update_layout(height=500, width=1200, title_text="Optimal Control Therapy for Cancer Treatment " + str(t1) + " :: " + str(t2) + " :: " + str(t3) + " :: " + str(t4)) 
            fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 1)
            fig.update_yaxes(title_text = "chig", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 1)
            fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 3)
            fig.update_yaxes(title_text = "chib", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 3)
            
            # third dose
            t_eval = np.linspace(t1+t2, t1+t2+t3, 80)
            Y = (odeint(pkmodel, xi, t_eval))

            fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 0], name = "chig: change in amount of Imatinib in the gastrointestinal tract at D = "+str(i)+"mg"), row=1, col=1)
            fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 1], name = "chib: change in the amount of Imatinib in the blood with time at D = "+str(i)+"mg"), row=1, col=3)
            fig.update_layout(height=500, width=1200, title_text="Optimal Control Therapy for Cancer Treatment " + str(t1) + " :: " + str(t2) + " :: " + str(t3) + " :: " + str(t4)) 
            fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 1)
            fig.update_yaxes(title_text = "chig", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 1)
            fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 3)
            fig.update_yaxes(title_text = "chib", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 3)
            
            # fourth dose
            t_eval = np.linspace(t1+t2+t3, t1+t2+t3+t4, 80)
            Y = (odeint(pkmodel, xi, t_eval))

            fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 0], name = "chig: change in amount of Imatinib in the gastrointestinal tract at D = "+str(i)+"mg"), row=1, col=1)
            fig.add_trace(go.Scatter(x=t_eval, y=Y[:, 1], name = "chib: change in the amount of Imatinib in the blood with time at D = "+str(i)+"mg"), row=1, col=3)
            fig.update_layout(height=500, width=1200, title_text="Optimal Control Therapy for Cancer Treatment " + str(t1) + " :: " + str(t2) + " :: " + str(t3) + " :: " + str(t4)) 
            fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 1)
            fig.update_yaxes(title_text = "chig", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 1)
            fig.update_xaxes(title_text = "t [hrs]", showline=True, linewidth=2, rangeslider_visible=True, linecolor='black', mirror=True, row = 1, col = 3)
            fig.update_yaxes(title_text = "chib", showline=True, linewidth=2, linecolor='black', mirror=True, row = 1, col = 3)
            
            fig.show()